<h2>Introduction</h2>
This notebook ultised msticpy to query EmailEvents table in Sentinel to final similiar Subject with provided one using difflib_similiar and Levenshtein.

In [25]:
import pandas as pd
import msticpy, os, json,difflib, Levenshtein
from msticpy.data.data_providers import QueryProvider
from msticpy.common.wsconfig import WorkspaceConfig
from datetime import date
from pathlib import Path
from msticpy.config import MpConfigFile, MpConfigEdit
import plotly.express as px




<h3>Login Azure via cli</h3>

In [4]:
#login azure
!az login --tenant 'TenantId'

<h3>msticpy config</h3>

In [ ]:
#config
mpfile = MpConfigFile()
mpedit = MpConfigEdit(settings=mpfile)
mpedit

<h3>Load config</h3>

In [8]:
mp_conf = "msticpyconfig.yaml"

# check if MSTICPYCONFIG is already an env variable otherwise use path from above
mp_env = os.environ.get("MSTICPYCONFIG")
mp_conf = mp_env if mp_env and Path(mp_env).is_file() else mp_conf

if not Path(mp_conf).is_file():
    print(
        "No msticpyconfig.yaml was found!",
        "Please check that there is a config.json file in your workspace folder.",
        "If this is not there, go back to the Microsoft Sentinel portal and launch",
        "this notebook from there.",
        sep="\n"
    )
else:
    mpedit = MpConfigEdit(mp_conf)
    mpconfig = MpConfigFile(mp_conf)
    # print(f"Configured Sentinel workspaces: {json.dumps(mpconfig.settings, indent=4)}") # Print the config

msticpy.settings.refresh_config()

Label(value='Loading. Please wait.')

In [10]:
def similar(a, b):
    return difflib.SequenceMatcher(None, a, b).ratio()

<h3>Connect Sentinel</h3>
Fill in workspace list and base subject

In [11]:
Workspaces=[]
subject =''
qry_prov = QueryProvider("MSSentinel_New")
qry_prov.connect(workspaces=Workspaces)

connected


In [13]:
query=""" EmailEvents  | where TimeGenerated >ago(1d) | where EmailDirection == 'Inbound' | limit 100000 """
results=qry_prov.exec_query(query)
results=results.groupby('Subject').size().reset_index(name='count')
results['similiar'] = results.apply( lambda row: similar(row['Subject'],subject), axis=1)
results['Lev'] = results.apply( lambda row: Levenshtein.ratio(row['Subject'],subject), axis=1)

In [ ]:
filteredResults=results[['Subject','similiar','Lev','count']]
filteredResults[filteredResults['similiar'] > 0.7].sort_values(by=['similiar'], ascending=False)

In [40]:
fig = px.scatter(results, x='similiar',y= 'Lev',hover_data=["Subject","count"])


fig.show()